# rf203_ranges
Fitting and plotting in sub ranges.




**Author:** Wouter Verkerke  
<i><small>This notebook tutorial was automatically generated with <a href= "https://github.com/root-project/root/blob/master/documentation/doxygen/converttonotebook.py">ROOTBOOK-izer</a> from the macro found in the ROOT repository  on Wednesday, April 17, 2024 at 11:17 AM.</small></i>

In [1]:
%%cpp -d
#include "RooRealVar.h"
#include "RooDataSet.h"
#include "RooGaussian.h"
#include "RooPolynomial.h"
#include "RooAddPdf.h"
#include "RooFitResult.h"
#include "RooPlot.h"
#include "TCanvas.h"
#include "TAxis.h"
#include "TH1.h"
using namespace RooFit;

Setup model
---------------------

Construct observables x

In [2]:
RooRealVar x("x", "x", -10, 10);

Construct gaussx(x,mx,1)

In [3]:
RooRealVar mx("mx", "mx", 0, -10, 10);
RooGaussian gx("gx", "gx", x, mx, 1.0);

Construct px = 1 (flat in x)

In [4]:
RooPolynomial px("px", "px", x);

Construct model = f*gx + (1-f)px

In [5]:
RooRealVar f("f", "f", 0., 1.);
RooAddPdf model("model", "model", RooArgList(gx, px), f);

Generated 10000 events in (x,y) from pdf model

In [6]:
std::unique_ptr<RooDataSet> modelData{model.generate(x, 10000)};

Fit full range
---------------------------

Fit pdf to all data

In [7]:
std::unique_ptr<RooFitResult> r_full{model.fitTo(*modelData, Save(true), PrintLevel(-1))};

[#1] INFO:Fitting -- RooAbsPdf::fitTo(model) fixing normalization set for coefficient determination to observables in data
[#1] INFO:Fitting -- using CPU computation library compiled with -mavx2
[#1] INFO:Fitting -- RooAddition::defaultErrorLevel(nll_model_modelData) Summation contains a RooNLLVar, using its error level
[#1] INFO:Minimization -- RooAbsMinimizerFcn::setOptimizeConst: activating const optimization
[#1] INFO:Minimization -- RooAbsMinimizerFcn::setOptimizeConst: deactivating const optimization


Fit partial range
----------------------------------

Define "signal" range in x as [-3,3]

In [8]:
x.setRange("signal", -3, 3);

[#1] INFO:Eval -- RooRealVar::setRange(x) new range named 'signal' created with bounds [-3,3]


Fit pdf only to data in "signal" range

In [9]:
std::unique_ptr<RooFitResult> r_sig{model.fitTo(*modelData, Save(true), Range("signal"), PrintLevel(-1))};

[#1] INFO:Eval -- RooRealVar::setRange(x) new range named 'fit_nll_model_modelData' created with bounds [-3,3]
[#1] INFO:Fitting -- RooAbsPdf::fitTo(model) fixing normalization set for coefficient determination to observables in data
[#1] INFO:Fitting -- RooAddition::defaultErrorLevel(nll_model_modelData) Summation contains a RooNLLVar, using its error level
[#1] INFO:Minimization -- RooAbsMinimizerFcn::setOptimizeConst: activating const optimization
[#1] INFO:Minimization -- RooAbsMinimizerFcn::setOptimizeConst: deactivating const optimization


Plot / print results
---------------------------------------

Make plot frame in x and add data and fitted model

In [10]:
RooPlot *frame = x.frame(Title("Fitting a sub range"));
modelData->plotOn(frame);
model.plotOn(frame, Range(""), LineStyle(kDashed), LineColor(kRed)); // Add shape in full ranged dashed
model.plotOn(frame);                                                     // By default only fitted range is shown

[#1] INFO:Plotting -- RooAbsPdf::plotOn(model) p.d.f was fitted in a subrange and no explicit NormRange() was specified. Plotting / normalising in fit range. To override, do one of the following
	- Clear the automatic fit range attribute: <pdf>.removeStringAttribute("fitrange");
	- Explicitly specify the plotting range: Range("<rangeName>").
	- Explicitly specify where to compute the normalisation: NormRange("<rangeName>").
	The default (full) range can be denoted with Range("") / NormRange("").
[#1] INFO:Plotting -- RooAbsPdf::plotOn(model) only plotting range ''
[#1] INFO:Plotting -- RooAbsPdf::plotOn(model) p.d.f. curve is normalized using explicit choice of ranges 'fit_nll_model_modelData'
[#1] INFO:Plotting -- RooAbsPdf::plotOn(model) p.d.f was fitted in a subrange and no explicit Range() and NormRange() was specified. Plotting / normalising in fit range. To override, do one of the following
	- Clear the automatic fit range attribute: <pdf>.removeStringAttribute("fitrange");
	- Ex

Print fit results

In [11]:
cout << "result of fit on all data " << endl;
r_full->Print();
cout << "result of fit in in signal region (note increased error on signal fraction)" << endl;
r_sig->Print();

result of fit on all data 

  RooFitResult: minimized FCN value: 25939.4, estimated distance to minimum: 3.77183e-06
                covariance matrix quality: Full, accurate covariance matrix
                Status : MINIMIZE=0 HESSE=0 

    Floating Parameter    FinalValue +/-  Error   
  --------------------  --------------------------
                     f    5.0441e-01 +/-  6.32e-03
                    mx   -2.1605e-02 +/-  1.77e-02

result of fit in in signal region (note increased error on signal fraction)

  RooFitResult: minimized FCN value: 10339.5, estimated distance to minimum: 0.000279216
                covariance matrix quality: Full, accurate covariance matrix
                Status : MINIMIZE=0 HESSE=0 

    Floating Parameter    FinalValue +/-  Error   
  --------------------  --------------------------
                     f    4.8979e-01 +/-  1.62e-02
                    mx   -2.1518e-02 +/-  1.79e-02



Draw frame on canvas

In [12]:
new TCanvas("rf203_ranges", "rf203_ranges", 600, 600);
gPad->SetLeftMargin(0.15);
frame->GetYaxis()->SetTitleOffset(1.4);
frame->Draw();

return;

Draw all canvases 

In [13]:
%jsroot on
gROOT->GetListOfCanvases()->Draw()